In [1]:
#from gensim.models import Word2Vec
import pandas as pd
import numpy as np
from scipy import sparse as sps
import nltk
import pickle
from sklearn.feature_extraction.text import TfidfVectorizer


In [2]:
saved = open("pickle/game_reviews.pickle","rb")
game_reviews = pickle.load(saved)
game_reviews.head()

funny                                          helpful  item_id last_edited  \
0                                         No ratings yet     1250               
1                                         No ratings yet    22200               
2                                         No ratings yet    43110               
3        15 of 20 people (75%) found this review helpful   251610               
4           0 of 1 people (0%) found this review helpful   227300               

                      posted  recommend  \
0   Posted November 5, 2011.       True   
1      Posted July 15, 2011.       True   
2     Posted April 21, 2011.       True   
3      Posted June 24, 2014.       True   
4  Posted September 8, 2013.       True   

                                              review            user_id  
0  Simple yet with great replayability. In my opi...  76561197970982479  
1               It's unique and worth a playthrough.  76561197970982479  
2  Great atmosphere. The gunplay can be a bit chu...  76561197970982479  
3  I know what you think when you see this title ...            js41637  
4  For a simple (it's actually not all that simpl...            js41637

In [23]:
item_data1 = pd.DataFrame({'review': game_reviews.groupby(['item_id']).review.apply(lambda x:' '.join(x))})
item_data1.reset_index(inplace=True)
item_data1.head()

item_id                                             review
0       10  Cool game Wallbang simulator this game is the ...
1       20  No Bread. Team Fortress tutkusunun başlangıcı;...
2       30  An excellent war shooter with a great online c...
3       40  Best playerbase I have ever met. Everybody is ...
4       50  You want a decent Half-Life 1 game that's chea...

In [3]:
user_item_count = pd.DataFrame({'Count': game_reviews.groupby(['user_id']).item_id.count()})
user_item_count = user_item_count.sort_values(by=['Count'], ascending = False)
user_item_count = user_item_count.reset_index()
user_sample= user_item_count[(user_item_count['Count'] > 2)]
user_table = pd.merge(user_sample, game_reviews, on='user_id', how='left')
#review_data = user_games.drop(['stemmed_reviews','notstemmed_reviews','stemmed_vec_reviews','notstemmed_vec_reviews'], axis = 1)
review_data_sample = user_table.sample(frac=0.1)
review_data_sample.head()

user_id  Count                             funny  \
25346   jefferyjefferson      4  1 person found this review funny   
12198            IrishNZ      7                                     
34515  76561198014841100      3                                     
21724           TomBlack      5                                     
11242           damo4lyf      7                                     

                                              helpful  item_id last_edited  \
25346                                  No ratings yet   255710               
12198                                  No ratings yet   418070               
34515                                  No ratings yet     1250               
21724                                  No ratings yet   311210               
11242  1 of 1 people (100%) found this review helpful      620               

                          posted  recommend  \
25346     Posted March 20, 2015.       True   
12198  Posted November 15, 2015.       True   
34515       Posted July 5, 2014.       True   
21724           Posted April 28.       True   
11242  Posted September 2, 2014.       True   

                                                  review  
25346  This is a great take on the city sim genre.Her...  
12198                                                Aee  
34515                                Strangely addictive  
21724  Although the multiplayer can get annoying at t...  
11242

In [4]:
#review_data = user_games.drop(['stemmed_reviews','notstemmed_reviews','stemmed_vec_reviews','notstemmed_vec_reviews'], axis = 1)
#review_data_sample = game_reviews.sample(frac=0.1)
#review_data_sample

In [3]:
game_reviews.shape

(58430, 8)

In [19]:
content = item_data1.loc[1]['review']

processed = tokenizer.tokenize(content)

processed = [token.lower() for token in processed]

processed = [token for token in processed if token not in stopwords.words('english')]

processed = [ps.stem(token) for token in processed]

In [4]:
from tf_idf import tf_idf

In [7]:
%%time
tf = tf_idf()
type(tf)
tf.fit(game_reviews)

CPU times: user 2min 44s, sys: 12.7 s, total: 2min 57s
Wall time: 2min 56s


In [9]:
%%time
itemList = [10,20,30,40,50,60,70,80]
score = tf.predict_for_user('IrishNZ', itemList)

CPU times: user 98.1 ms, sys: 3.86 ms, total: 102 ms
Wall time: 99.5 ms


In [10]:
score

item_id
10    1.572849
20    1.231242
30    0.795691
40    0.524959
50    0.908800
60    0.968645
70    1.653735
80    0.670783
dtype: float64

In [32]:
itemList = [10,20,30,40]

predList = score.filter(items=itemList)
final_score = predList.sum(axis=0)
#predList 
final_score

item_id
10    1.572849
20    1.231242
30    0.795691
40    0.524959
dtype: float64

In [13]:
score[105600]

0    0.405470
1    0.313523
2    0.437275
3    0.240273
4    0.187153
5    0.452412
6    0.192569
Name: 105600, dtype: float64

In [11]:
score[105600].sum()

2.2286743730164433

In [11]:
user_item_ids = game_reviews.set_index('user_id')['item_id']
temp_df = user_item_ids.loc['js41637'].to_frame()
temp_df = temp_df.reset_index()
items = temp_df[:]['item_id']
items

0    251610
1    227300
2    239030
Name: item_id, dtype: int64

In [7]:
type(review_data_sample)

pandas.core.frame.DataFrame

In [35]:
file1 = open("pickle/steam_preprocessed_data.pkl","rb")
steam_reviews = pickle.load(file1)
steam_reviews.head()

item_id                                            reviews  \
0       10  Cool game Wallbang simulator this game is the ...   
1       20  No Bread. Team Fortress tutkusunun başlangıcı;...   
2       30  An excellent war shooter with a great online c...   
3       40  Best playerbase I have ever met. Everybody is ...   
4       50  You want a decent Half-Life 1 game that's chea...   

                                     stemmed_reviews  \
0  [cool, game, wallbang, simulator, game, 1, onl...   
1  [bread, team, fortress, tutkusunun, başlangıcı...   
2  [excellent, war, shooter, great, online, commu...   
3  [best, playerbase, ever, met, everybody, nice,...   
4  [want, decent, half, life, 1, game, cheap, get...   

                                  notstemmed_reviews  \
0  [cool, game, wallbang, simulator, game, 1, onl...   
1  [bread, team, fortress, tutkusunun, başlangıcı...   
2  [excellent, war, shooter, great, online, commu...   
3  [best, playerbase, ever, met, everybody, nice,...   
4  [want, decent, half, life, 1, game, cheap, get...   

                                 stemmed_vec_reviews  \
0  [0.05077233, 0.035106, 0.035813432, 0.08294137...   
1  [0.064550705, 0.043155234, 0.016609283, 0.0941...   
2  [0.07194577, 0.028747173, 0.004573098, 0.09898...   
3  [0.059004042, 0.012017144, 0.04434543, 0.15011...   
4  [0.05373419, 0.022838775, -0.015340169, 0.1084...   

                              notstemmed_vec_reviews  \
0  [0.05077233, 0.035106, 0.035813432, 0.08294137...   
1  [0.064550705, 0.043155234, 0.016609283, 0.0941...   
2  [0.07194577, 0.028747173, 0.004573098, 0.09898...   
3  [0.059004042, 0.012017144, 0.04434543, 0.15011...   
4  [0.06585138, 0.013633034, -0.020324707, 0.1096...   

                   item_name  
0             Counter-Strike  
1      Team Fortress Classic  
2              Day of Defeat  
3         Deathmatch Classic  
4  Half-Life: Opposing Force

In [16]:
r_index = pd.Index(game_reviews_combined.item_id.unique(), name='item_id')

In [18]:
#item2index = itemid_2_index(game_reviews_combined)
idx = r_index.get_loc(227300)
idx

1170

In [23]:
game_reviews_combined.iloc[1170]

item_id                                               227300
reviews    For a simple (it's actually not all that simpl...
Name: 1170, dtype: object

In [13]:
game_reviews_combined = pd.DataFrame({'reviews': game_reviews.groupby(['item_id']).review.apply(lambda x:' '.join(x))})
game_reviews_combined.reset_index(inplace=True)

In [14]:
game_reviews_combined.head()

item_id                                            reviews
0       10  Cool game Wallbang simulator this game is the ...
1       20  No Bread. Team Fortress tutkusunun başlangıcı;...
2       30  An excellent war shooter with a great online c...
3       40  Best playerbase I have ever met. Everybody is ...
4       50  You want a decent Half-Life 1 game that's chea...

In [3]:
file2= open("pickle/user_games.pickle","rb")
#user_games = pd.read_csv('csv/steam/user_games.csv')
#user_games.set_index('user_id', inplace = True)
user_game = pickle.load(file2)
user_game.head()

user_id  item_id                  item_name
0  76561197970982479       10             Counter-Strike
1  76561197970982479       20      Team Fortress Classic
2  76561197970982479       30              Day of Defeat
3  76561197970982479       40         Deathmatch Classic
4  76561197970982479       50  Half-Life: Opposing Force

In [4]:
steam_reviews = steam_reviews.drop(columns=['item_name'])
user_games = pd.merge(steam_reviews, user_game, on='item_id', how='left')
user_games.head()

item_id                                            reviews  \
0       10  Cool game Wallbang simulator this game is the ...   
1       10  Cool game Wallbang simulator this game is the ...   
2       10  Cool game Wallbang simulator this game is the ...   
3       10  Cool game Wallbang simulator this game is the ...   
4       10  Cool game Wallbang simulator this game is the ...   

                                     stemmed_reviews  \
0  [cool, game, wallbang, simulator, game, 1, onl...   
1  [cool, game, wallbang, simulator, game, 1, onl...   
2  [cool, game, wallbang, simulator, game, 1, onl...   
3  [cool, game, wallbang, simulator, game, 1, onl...   
4  [cool, game, wallbang, simulator, game, 1, onl...   

                                  notstemmed_reviews  \
0  [cool, game, wallbang, simulator, game, 1, onl...   
1  [cool, game, wallbang, simulator, game, 1, onl...   
2  [cool, game, wallbang, simulator, game, 1, onl...   
3  [cool, game, wallbang, simulator, game, 1, onl...   
4  [cool, game, wallbang, simulator, game, 1, onl...   

                                 stemmed_vec_reviews  \
0  [0.05077233, 0.035106, 0.035813432, 0.08294137...   
1  [0.05077233, 0.035106, 0.035813432, 0.08294137...   
2  [0.05077233, 0.035106, 0.035813432, 0.08294137...   
3  [0.05077233, 0.035106, 0.035813432, 0.08294137...   
4  [0.05077233, 0.035106, 0.035813432, 0.08294137...   

                              notstemmed_vec_reviews            user_id  \
0  [0.05077233, 0.035106, 0.035813432, 0.08294137...  76561197970982479   
1  [0.05077233, 0.035106, 0.035813432, 0.08294137...            js41637   
2  [0.05077233, 0.035106, 0.035813432, 0.08294137...         Riot-Punch   
3  [0.05077233, 0.035106, 0.035813432, 0.08294137...              doctr   
4  [0.05077233, 0.035106, 0.035813432, 0.08294137...     corrupted_soul   

        item_name  
0  Counter-Strike  
1  Counter-Strike  
2  Counter-Strike  
3  Counter-Strike  
4  Counter-Strike

In [36]:
corpus_list = []
for item in steam_reviews['stemmed_reviews']:
    #corpus_list.append(' '.join(item))
    corpus_list.append(item)

In [37]:
corpus_list

[['cool',
  'game',
  'wallbang',
  'simulator',
  'game',
  '1',
  'online',
  'action',
  'game',
  'awesome',
  'better',
  'team',
  'fortress',
  'games',
  'mutiplit',
  'player',
  'games',
  'best',
  'fps',
  'game',
  'one',
  'best',
  'childhood',
  'games',
  'ever',
  'played',
  '10',
  '10',
  'que',
  'decir',
  'de',
  'este',
  'gran',
  'juego',
  'comence',
  'jugarlo',
  'alla',
  'por',
  '2002',
  'vuelto',
  'jugarlo',
  'ahora',
  'satisface',
  'tanto',
  'como',
  'antes',
  'people',
  'still',
  'play',
  'siq',
  'game',
  '2gud4u',
  'better',
  'csgo',
  'first',
  'online',
  'shooter',
  'played',
  'find',
  'impossible',
  'improve',
  'game',
  'way',
  'please',
  'put',
  'australian',
  'servers',
  'cs',
  '1',
  '6',
  'espeacially',
  'cod',
  'mod',
  'would',
  'nice',
  'simplismente',
  'perfeito',
  'lol',
  'gyertek',
  'gamelni',
  'mindenki',
  'itt',
  'van',
  'aki',
  'számit',
  'best',
  'game',
  'ever',
  'world',
  'best',
  '

In [15]:
games = user_games[['item_id', 'item_name']].drop_duplicates()
assert games.index.is_unique
games.head()

item_id                  item_name
0           10             Counter-Strike
9611        20      Team Fortress Classic
15879       30              Day of Defeat
19310       40         Deathmatch Classic
22552       50  Half-Life: Opposing Force

In [ ]:
from evaluation_func import vec_mat
from evaluation_func import tf_idf
from evaluation_func import itemid_2_index
from evaluation_func import cosine_sim
from evaluation_func import score_reviews
from evaluation_func import topn
from evaluation_func import get_user_item
from evaluation_func import multi_score
from evaluation_func import recommendation
from evaluation_func import hit_rate


In [16]:
from tf_idf_cosine import tf_idf_cosine_topn
from tf_idf_cosine import recommendation
from tf_idf_cosine import tf_idf

## Split

In [17]:
user_item_count = pd.DataFrame({'Count': user_games.groupby(['user_id']).item_id.count()})
user_item_count = user_item_count.sort_values(by=['Count'], ascending = False)
user_item_count = user_item_count.reset_index()
user_sample= user_item_count[(user_item_count['Count'] > 10)]
user_table = pd.merge(user_sample, user_games, on='user_id', how='left')
users = user_table['user_id'].sample(n= 20, random_state=10).values

In [18]:
users

array(['76561198072171461', '76561198095856407', 'mine4yourself',
       '76561198028666719', 'Qinsmoon8080', 'Stagdage', 'kilroy_maddog',
       '76561198064263168', '76561198101521395', '23142433253545',
       '76561197968307794', '76561198005827838', 'alienc', 'thavleifrim',
       '76561197988762135', '76561198061295353', 'HollowerX',
       '76561198050352271', 'absolutezero', '76561198053799686'],
      dtype=object)

In [19]:
topn = tf_idf_cosine_topn(user_games, games, steam_reviews, 'stemmed_reviews', '76561198072171461')
topn

item_id                               item_name
0   239820                         Game Dev Tycoon
1   208090                                 Loadout
2   243870  Tom Clancy's Ghost Recon Phantoms - NA
3   346110                   ARK: Survival Evolved
4   204360                         Castle Crashers
5   295110                      H1Z1: Just Survive
6   113200                    The Binding of Isaac
7   224260                    No More Room in Hell
8   242760                              The Forest
9   248820                            Risk of Rain

In [21]:
a = tf_idf(steam_reviews, 'stemmed_reviews')

In [34]:
b = a.todense()